# Reading and Writing Data ( Extract Step )

- Produce Spark code in Databricks using Jupyter Notebooks and Python scripts

  _The notebook should contain Python code to extract information from CSV files stored in Databricks and write it to the Delta file system._

- Use distributed data storage using Azure Data Storage options

  _The notebook should contain Python code that picks files up from the Databricks file system storage and writes it out to Delta file locations._
  

In [0]:
# The snippets bellow can be used to relocate the ingested files if necessary since the script below assumes the files are located at: "/FileStore/csv_files"

# To create the path used on this script: 
# dbutils.fs.mkdirs("/FileStore/csv_files")

# To delete and move files and paths case necessary:
# dbutils.fs.rm('/delta/staging', recurse=True)
# dbutils.fs.mv("/old_location/file.csv", "/new_location")

True

In [0]:
from pyspark.sql.types import *


rider_schema = StructType([
    StructField("rider_id", LongType(), True),
    StructField("first", StringType(), True),
    StructField("last", StringType(), True),
    StructField("address", StringType(), True),
    StructField("birthday", DateType(), True),
    StructField("account_start_date", DateType(), True),
    StructField("account_end_date", DateType(), True),
    StructField("is_member", BooleanType(), True)
])

payment_schema = StructType([
    StructField("payment_id", LongType(), True),
    StructField("date", DateType(), True),
    StructField("amount", DecimalType(25, 2), True),
    StructField("rider_id", LongType(), True)
])

trip_schema = StructType([
    StructField("trip_id", StringType(), True),
    StructField("rideable_type", StringType(), True),
    StructField("start_at", TimestampNTZType(), True),
    StructField("ended_at", TimestampNTZType(), True),
    StructField("start_station_id", StringType(), True),
    StructField("end_station_id", StringType(), True),
    StructField("rider_id", LongType(), True)
])

station_schema = StructType([
    StructField("station_id", StringType(), True),
	StructField("name", StringType(), True),
	StructField("latitude", DoubleType(), True),
	StructField("longitude", DoubleType(), True)
])

files = [("trips", trip_schema), ("stations", station_schema), ("payments", payment_schema), ("riders", rider_schema)]
for file, schema in files:
    file_path = f"/FileStore/csv_files/{file}.csv"
    out_path = f"dbfs:/delta/staging/{file}"

    spark_df = spark.read\
                .format("csv")\
                .option("header", False)\
                .option("inferSchema", False)\
                .option("delimiter", ",")\
                .schema(schema)\
                .load(file_path)

    spark_df.write.format("delta").mode("overwrite").save(out_path)

In [0]:
# Use to check if the data was loaded correctly into delta
result = spark.read.format("delta").load('/delta/staging/stations')
display(result)

station_id name latitude longitude] 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669 KP1705001026 LaSalle Dr & Huron St 41.894877 -87.632326 13253 Lincoln Ave & Waveland Ave 41.948797 -87.675278 KA1503000044 Rush St & Hubbard St 41.890173 -87.62618499999999 KA1504000140 Winchester Ave & Elston Ave 41.92403733333333 -87.67641483333334 TA1305000032 Clinton St & Madison St 41.882242 -87.64106600000001 TA1306000012 Wells St & Huron St 41.89475366666667 -87.63440200000001 13133 Damen Ave & Cortland St 41.915983000000004 -87.677335 SL-005 Indiana Ave & Roosevelt Rd 41.867888 -87.623041 13235 Southport Ave & Waveland Ave 41.94815 -87.66394 TA1307000139 MLK Jr Dr & 29th St 41.842052 -87.617 TA1305000009 Clark St & Ida B Wells Dr 41.8759326655 -87.63058453549999 13276 Stockton Dr & Wrightwood Ave 41.9313455 -87.63869133333333 TA1307000107 Sheridan Rd & Montrose Ave 41.96167 -87.65464 13193 Larrabee St & Webster Ave 41.921822 -87.64414000000001 KA1503000072 Wacker Dr & Washington St 41.883132 -87.637321 TA1307000166 Halsted St & Willow St 41.913865 -87.64875500000001 13285 Wood St & Taylor St (Temp) 41.86926521843819 -87.67373085021973 TA1306000016 Sheffield Ave & Fullerton Ave 41.92552516666667 -87.65368583333333 13303 Clark St & Chicago Ave 41.89675 -87.63089000000001 15575 Broadway & Thorndale Ave 41.98974251144 -87.6601406209 623 Michigan Ave & 8th St 41.872287666666665 -87.6239145 TA1309000050 Lincoln Ave & Addison St 41.946176 -87.67330799999999 15445 Wentworth Ave & 33rd St 41.83452988563 -87.63182298139999 13164 Racine Ave & 18th St 41.858166 -87.65649499999999 TA1307000151 Wells St & Hubbard St 41.889905999999996 -87.634266 13158 Peoria St & Jackson Blvd 41.877641596275296 -87.64961779117584 13150 Michigan Ave & 18th St 41.857813 -87.62455 TA1308000036 Indiana Ave & 31st St 41.83884433333333 -87.62183783333332 TA1308000013 Halsted St & Archer Ave 41.847203 -87.646795 TA1306000013 New St & Illinois St 41.89084704062381 -87.6186168193817 13061 Ashland Ave & Division St 41.90345 -87.66774699999999 TA1307000048 Fort Dearborn Dr & 31st St 41.838556 -87.60821800000001 TA1308000045 Wallace St & 35th St 41.830628999999995 -87.64129 13206 Loomis St & Jackson Blvd 41.877945000000004 -87.66200699999999 13156 Aberdeen St & Monroe St 41.880419 -87.655519 TA1306000015 Morgan St & Lake St 41.8854833079 -87.6523048564 13058 Dayton St & North Ave 41.9105780349 -87.6494219288 TA1309000008 Franklin St & Adams St (Temp) 41.879434091400135 -87.63550400733948 KA1504000135 Wells St & Elm St 41.90320733333333 -87.63461616666666 KA1503000064 Dusable Harbor 41.886976000000004 -87.612813 TA1305000022 Orleans St & Merchandise Mart Plaza 41.888243 -87.63639 KA1504000079 Larrabee St & Division St 41.90348607004 -87.6433534936 KA1503000022 Clark St & Montrose Ave 41.961588 -87.666036 13109 Broadway & Berwyn Ave 41.978353000000006 -87.65975300000001 15530 Rush St & Superior St 41.89576474564 -87.62590803270001 TA1306000010 Daley Center Plaza 41.884240999999996 -87.629634 13146 Clark St & Armitage Ave 41.918306 -87.636282 15578 Broadway & Ridge Ave 41.9840446107 -87.66027382950001 KA1503000034 LaSalle St & Adams St 41.87934437346 -87.63198522129998 KA1503000059 Lake Park Ave & 53rd St 41.79949429373 -87.5864498959 TA1305000011 Michigan Ave & Lake St 41.886024 -87.624117 TA1307000061 State St & Pearson St 41.897448 -87.628722 SL-011 Wells St & Polk St 41.872596 -87.63350200000001 TA1309000010 Wabash Ave & 9th St 41.8702615 -87.62538516666666 15534 Field Blvd & South Water St 41.88634906269 -87.6175165471 TA1307000119 Clarendon Ave & Leland Ave 41.967968 -87.650001 TA1305000029 State St & Randolph St 41.884730200599996 -87.6277335692 TA1309000063 Lake Park Ave & 56th St 41.793242 -87.58778199999999 KA1504000133 Rush St & Ce

# Loading Data from Delta ( Load Step )

- Implement key features of data lakes on Azure

  The notebook should contain code that creates tables and loads data from Delta files. The learner should use spark.sql statements to create the tables and then load data from the files that were extracted in the Extract step.
  

In [0]:
tables_name = ["stations", "riders", "payments", "trips"]
for name in tables_name:
  location_path = f"'/delta/staging/{name}'"
  spark.sql(f"CREATE TABLE IF NOT EXISTS staging_{name} USING DELTA LOCATION {location_path}")

In [0]:
# Use to check if data as properly loaded to tables
table_result = spark.sql(f"SELECT * FROM staging_{tables_name[0]} LIMIT 10")
display(table_result)

station_id name latitude longitude 525 Glenwood Ave & Touhy Ave 42.012701 -87.66605799999999 KA1503000012 Clark St & Lake St 41.88579466666667 -87.63110066666668 637 Wood St & Chicago Ave 41.895634 -87.672069 13216 State St & 33rd St 41.8347335 -87.6258275 18003 Fairbanks St & Superior St 41.89580766666667 -87.62025316666669 KP1705001026 LaSalle Dr & Huron St 41.894877 -87.632326 13253 Lincoln Ave & Waveland Ave 41.948797 -87.675278 KA1503000044 Rush St & Hubbard St 41.890173 -87.62618499999999 KA1504000140 Winchester Ave & Elston Ave 41.92403733333333 -87.67641483333334 TA1305000032 Clinton St & Madison St 41.882242 -87.64106600000001

# Transforming Data to Gold ( Transfom Step )

- Use Spark and Databricks to run ELT processes by creating fact tables

  The fact table Python scripts should contain appropriate keys from the dimensions. In addition, the fact table scripts should appropriately generate the correct facts based on the diagrams provided in the first step.
  
- Use Spark and Databricks to run ELT processes by creating dimension tables

  The dimension Python scripts should match the schema diagram. Dimensions should generate appropriate keys and should not contain facts.

- Produce Spark code in Databricks using Jupyter Notebooks and Python scripts

  The transform scripts should at minimum adhere to the following: should write to delta; should use overwrite mode; save as a table in delta.

### Date Dimension Tranformation

In [0]:
date_dim_df = spark.sql("""
SELECT DISTINCT *
    FROM
    (
        Select  cast(start_at AS VARCHAR(20)) as date_id,
                year(start_at) as year,
                quarter(start_at) as quarter,
                month(start_at) as month,
                day(start_at) as day,
                weekday(start_at) weekday,
                hour(start_at) hour,
                minute(start_at) minute,
                second(start_at) second
        From staging_trips
        UNION ALL
        Select  cast(ended_at AS VARCHAR(20)) as date_id,
                year(ended_at) as year,
                quarter(ended_at) as quarter,
                month(ended_at) as month,
                day(ended_at) as day,
                weekday(ended_at) weekday,
                hour(ended_at) hour,
                minute(ended_at) minute,
                second(ended_at) second
        From staging_trips
        UNION ALL
        Select  cast(date AS VARCHAR(20)) as date_id,
                year(date) as year,
                quarter(date) as quarter,
                month(date) as month,
                day(date) as day,
                weekday(date) weekday,
                00 as hour,
                00 as minute,
                00 as second
        From staging_payments
    ) as temp
""")

date_dim_df.write.format("delta").mode("overwrite").saveAsTable("date_dim")
display(date_dim_df)

### Station Dimension Tranformation

In [0]:
stations_dim_df = spark.sql("""
SELECT DISTINCT station_id,
                name        AS station_name,
                latitude    AS station_latitude,
                longitude   AS station_longitude
	       FROM staging_stations
""")

stations_dim_df.write.format("delta").mode("overwrite").saveAsTable("station_dim")
display(stations_dim_df)

### Rider Dimention Tranformation

In [0]:
riders_dim_df = spark.sql("""
SELECT DISTINCT rider_id,
                concat('', first, last)                         AS rider_name,
                datediff(YEAR, birthday, account_start_date)	AS rider_age,
                birthday                                        AS rider_birthday,
                account_start_date                              AS rider_join_date,
                is_member
	FROM staging_riders
""")

riders_dim_df.write.format("delta").mode("overwrite").saveAsTable("rider_dim")
display(riders_dim_df)

rider_id rider_name rider_age rider_birthday rider_join_date is_member 1030 JeremyRoberts 20 2000-05-13 2021-02-09 true 1200 ScottMorris 26 1995-10-29 2021-12-17 true 1495 MaryBecker 19 2001-06-15 2020-12-21 true 1578 AlyssaTerrell 12 2003-07-05 2015-12-24 true 1827 MelanieParker 64 1955-12-18 2020-06-04 false 1959 DouglasHicks 13 2003-07-25 2017-03-12 false 2109 MelissaVasquez 23 1994-04-16 2017-09-21 true 2272 LisaGonzales 23 1997-03-05 2020-11-24 true 2535 BettyGarner 22 1996-02-20 2018-03-09 true 2554 BrendaHampton 34 1985-02-13 2019-12-15 true 2838 ChristinaBartlett 29 1986-11-06 2016-06-24 true 3063 MeganFuentes 28 1992-05-13 2020-12-30 false 3343 SteveMiller 36 1985-04-18 2021-08-04 true 3354 EmilyThompson 10 2005-01-04 2015-11-06 true 4600 EdwardHernandez 19 1998-05-08 2017-09-26 true 4788 LuisEdwards 40 1980-10-16 2021-03-15 true 4975 CindyBryant 20 1996-06-20 2017-04-17 true 5366 AngelaWood 41 1977-02-24 2019-01-28 false 5502 SusanDavis 45 1970-12-30 2016-05-20 true 5542 MichelleHall 39 1977-12-03 2017-10-31 true 5668 MichelleAllen 37 1982-04-15 2019-04-22 false 5903 CalebBruce 20 2000-08-24 2020-08-24 true 6556 JohnClark 24 1997-01-29 2021-07-18 false 6898 StephanieBowen 43 1974-06-15 2018-03-22 true 6909 BrandonJones 40 1979-01-15 2019-09-14 true 7192 JohnBradford 31 1986-04-20 2017-05-20 false 7292 CharlesEvans 32 1984-07-11 2016-07-30 true 7361 ChristopherPoole 38 1983-09-28 2021-12-10 false 7364 KevinMorris 41 1978-04-06 2020-03-29 true 7656 CharlesPreston 44 1974-05-25 2018-10-10 true 7739 KevinWeiss 24 1997-06-16 2022-02-06 false 7842 MadisonRamirez 50 1969-04-02 2019-07-16 true 7855 MarkHanson 16 2004-10-02 2021-02-06 true 7972 DavidDominguez 28 1991-11-25 2020-06-30 true 8223 LauraJackson 22 1996-04-08 2019-03-01 true 8428 FrederickDixon 20 1995-09-22 2015-09-27 true 8443 JessicaStewart 36 1980-05-30 2017-02-02 true 8521 BenjaminDay 31 1990-05-17 2021-10-20 true 8610 DarylNelson 41 1980-04-10 2021-12-15 false 8813 MariaWilliams 28 1990-11-10 2018-12-05 true 8908 BrandonDavis 33 1986-05-22 2020-03-30 true 9032 LauraWest 20 2001-07-19 2022-02-09 true 9536 KristaMoody 8 2005-09-11 2014-07-30 true 9619 MaryKline 26 1986-10-06 2013-06-25 true 9650 MatthewShields 27 1994-03-29 2021-07-17 true 9718 DeanJenkins 32 1983-06-17 2016-02-29 false 9778 ScottChavez 49 1970-07-07 2020-03-14 true 9935 GregSnow 19 1995-12-11 2015-10-28 true 10060 JustinCarter 29 1990-05-13 2020-02-05 false 10429 MatthewMoore 19 2002-11-17 2021-11-26 false 10894 BethAnderson 36 1981-11-14 2018-03-18 false 11168 JenniferAllison 29 1991-05-24 2020-10-04 false 11301 AndreaPatton 34 1985-01-04 2019-12-31 true 11330 AlexandriaGarcia 19 1996-07-04 2016-01-23 false 11661 KarenCooper 37 1984-04-04 2021-11-26 true 12008 RonaldOliver 18 1999-12-29 2018-05-31 true 12164 ManuelRogers 27 1989-11-19 2017-01-01 true 12202 GaryHart 45 1971-04-10 2016-05-17 true 12308 JuanPreston 42 1978-05-19 2020-11-22 true 12364 KimberlyGolden 19 2000-07-14 2020-03-11 false 12542 MatthewHardy 14 2003-04-04 2017-06-21 true 12590 MichaelMontes 31 1990-09-27 2021-10-27 true 12760 BrianMcgee 31 1989-12-22 2021-04-11 true 12792 JillBray 46 1972-05-29 2019-02-21 true 12841 StevenStephens 49 1972-08-19 2021-12-25 true 12978 KelseySmith 40 1980-02-12 2020-09-21 true 1113 AnneNunez 27 1993-11-22 2021-09-23 true 1145 AnnaAllen 37 1982-11-07 2020-10-26 true 1217 MargaretSanchez 25 1994-12-01 2020-08-02 true 1258 JustinWilliams 30 1990-08-27 2021-05-23 true 1369 WendyNovak 40 1981-08-19 2022-02-04 true 1411 StevenSullivan 29 1991-09-20 2021-07-09 true 1427 AaronOsborn 33 1984-04-11 2017-12-04 true 1825 GabrielFerguson 15 2003-02-02 2018-12-09 true 1978 LauraHayes 27 1992-07-06 2020-06-01 true 2198 JillBridges 27 1993-06-19 2020-08-29 true 2353 ThomasBennett 43 1972-06-14 2016-06-06 false 2449 EdwinColeman 33 1987-11-16 2021-08-13 true 2797 DonnaLynch 34 1987-03-16 2021-05-11 false 2926 TinaBoyd 17 2000-09-15 2018-08-05 true 3086 MarkBailey 34 1981-07-22 2015-12-29 true 3113 ScottHarris

### Trips Fact Transformation

In [0]:
trips_fact_df = spark.sql("""
SELECT	t.trip_id,
        datediff(MINUTE, t.start_at, t.ended_at)    AS trip_duration_min,
        cast(t.start_at AS VARCHAR(20))             AS start_date_id,
        cast(t.ended_at AS VARCHAR(20))             AS ended_date_id,
        t.start_station_id,
        t.end_station_id,
        datediff(YEAR, r.rider_birthday, t.start_at)	    AS rider_age,
        r.rider_id
   FROM	staging_trips t
   JOIN station_dim s1 ON t.start_station_id = s1.station_id
   JOIN station_dim s2 ON t.end_station_id = s2.station_id
   JOIN rider_dim r    ON t.rider_id = r.rider_id
""")

trips_fact_df.write.format("delta").mode("overwrite").saveAsTable("trip_fact")
display(trips_fact_df)

trip_id trip_duration_min start_date_id ended_date_id start_station_id end_station_id rider_age rider_id 222BB8E5059252D7 18 2021-06-13 09:48:47 2021-06-13 10:07:23 KA1503000064 13021 30 34062 1826E16CB5486018 5 2021-06-21 22:59:13 2021-06-21 23:04:29 TA1306000010 13021 26 5342 3D9B6A0A5330B04D 5 2021-06-18 16:06:42 2021-06-18 16:12:02 TA1305000030 13021 26 3714 07E82F5E9C9E490F 16 2021-06-17 16:46:23 2021-06-17 17:02:45 TA1305000034 13021 18 18793 A8E94BAECBF0C2DD 54 2021-06-13 17:36:29 2021-06-13 18:30:39 TA1308000009 TA1308000009 28 43342 378F4AB323AA1D14 46 2021-06-13 13:20:10 2021-06-13 14:06:14 TA1308000009 TA1308000009 28 6693 38AD311DC2EB1FBE 14 2021-06-16 17:14:30 2021-06-16 17:28:34 KA1503000019 KA1503000019 56 71480 1D466737F0B18097 34 2021-06-27 14:51:52 2021-06-27 15:26:39 TA1308000009 TA1308000009 40 50846 27E1142E1ACFAEFB 0 2021-06-21 13:58:26 2021-06-21 13:58:53 13257 13257 21 18951 67F2A115DAE77924 16 2021-06-22 00:51:43 2021-06-22 01:08:25 TA1308000009 TA1308000009 37 63987 D30A0F588CAB9948 24 2021-06-03 16:40:02 2021-06-03 17:04:22 13036 13434 39 52600 B6D051538810CE8A 36 2021-06-14 19:19:04 2021-06-14 19:55:54 KA1503000064 TA1308000009 21 58393 9724F787201C914E 19 2021-06-06 19:37:03 2021-06-06 19:56:22 13042 13434 28 45636 5C07EC15B5E1F93C 10 2021-06-19 20:17:01 2021-06-19 20:27:19 13084 13257 30 66194 1BFBE159F63DF1AF 2 2021-06-30 09:06:25 2021-06-30 09:09:11 KA1503000043 13021 32 18576 C63897EB5765B1E6 2 2021-06-11 22:46:36 2021-06-11 22:49:03 TA1306000003 13021 39 62971 AAA3B86E0B459EBB 7 2021-06-10 15:56:15 2021-06-10 16:03:51 KA1503000043 13434 33 8235 B22FA59E25D85FFB 6 2021-06-10 17:20:02 2021-06-10 17:26:05 13157 13021 46 51431 ADA725E548D6CF84 7 2021-06-08 16:12:24 2021-06-08 16:19:32 KA1503000043 13434 36 40507 AC061F7C81D386EE 10 2021-06-25 10:04:56 2021-06-25 10:15:01 13016 13021 24 67393 92AFE274FABD11CE 15 2021-06-05 12:01:26 2021-06-05 12:17:16 KA17018054 13021 18 16460 3256D982124A51CC 12 2021-06-04 19:00:27 2021-06-04 19:12:47 657 13257 24 75162 F863618B48098D75 3891 2021-06-03 01:16:01 2021-06-05 18:07:36 13059 13021 34 13478 71DE5B8A7F699133 12 2021-06-11 20:58:10 2021-06-11 21:10:53 TA1307000164 TA1308000009 48 62165 F27720C77BF53D45 18 2021-06-02 19:00:27 2021-06-02 19:18:29 TA1309000033 13257 24 72120 70450A18BC3E1D2C 14 2021-06-26 23:05:28 2021-06-26 23:20:08 KA1503000043 13434 36 40507 67D4F59EF1AF0860 7 2021-06-14 15:39:18 2021-06-14 15:46:29 KA1503000043 13434 38 38429 E3C9A476285BCAC6 117 2021-06-27 12:18:43 2021-06-27 14:15:43 13042 TA1308000009 20 32429 FD52122A0097A531 2 2021-06-01 16:37:20 2021-06-01 16:39:29 WL-012 13021 58 65021 62488E6B93B305DC 59 2021-06-18 19:52:27 2021-06-18 20:51:45 WL-012 13021 21 42347 C2B3554CF7143205 9 2021-06-19 02:05:11 2021-06-19 02:14:15 TA1309000029 13257 27 22598 65DF68F8CFF425AC 37 2021-06-09 18:30:03 2021-06-09 19:07:43 TA1307000128 13257 22 54690 0FB0BE3484716E54 5 2021-06-08 22:50:01 2021-06-08 22:55:21 TA1305000022 13021 38 13575 695E965A2C32C219 21 2021-06-20 15:32:28 2021-06-20 15:53:48 518 13257 51 21558 CC5F8FDFD92095F0 20 2021-06-08 13:09:35 2021-06-08 13:30:14 KA1504000135 13257 42 65266 6D860D9BBE025B69 11 2021-06-18 16:46:00 2021-06-18 16:57:01 KA1504000135 13021 35 48144 F7B56023FD693D70 10 2021-06-01 13:34:50 2021-06-01 13:45:24 TA1307000128 13021 20 49504 255C4D03ABFE2986 12 2021-06-21 08:46:32 2021-06-21 08:58:42 657 13021 23 20626 8196B8C3543C9B67 20 2021-06-12 11:22:07 2021-06-12 11:42:57 518 13257 46 66950 E75063B987852D07 16 2021-06-12 18:19:09 2021-06-12 18:36:03 TA1307000163 13257 25 56559 FD35331CB15B3641 9 2021-06-19 14:01:41 2021-06-19 14:11:30 TA1305000041 13257 24 14642 ADAD41686143BC86 7 2021-06-22 07:25:15 2021-06-22 07:32:31 TA1305000041 13434 30 74049 7570A7E6445F89AA 9 2021-06-15 07:21:46 2021-06-15 07:31:22 TA1308000049 13021 18 51662 99824A4FFA681795 12 2021-06-15 21:01:11 2021-06-15 21:14:09 KA1504000135 13434 56 68386 BEDEC5C350675774 26 2021-06-07 20:25:54 2021-06-07 20:52:51 13071 13257 36 41143 3E0825E3

### Payments Fact Tranformation

In [0]:
payments_fact_df = spark.sql("""
     SELECT p.payment_id,
            p.amount,
            r.rider_id,
            cast(p.date AS VARCHAR(20)) AS payment_date_id
       FROM staging_payments p
       JOIN rider_dim r ON p.rider_id = r.rider_id
""")

payments_fact_df.write.format("delta").mode("overwrite").saveAsTable("payment_fact")
display(payments_fact_df)

payment_id amount rider_id payment_date_id 1 9.00 1000 2019-05-01 2 9.00 1000 2019-06-01 3 9.00 1000 2019-07-01 4 9.00 1000 2019-08-01 5 9.00 1000 2019-09-01 6 9.00 1000 2019-10-01 7 9.00 1000 2019-11-01 8 9.00 1000 2019-12-01 9 9.00 1000 2020-01-01 10 9.00 1000 2020-02-01 11 9.00 1000 2020-03-01 12 9.00 1000 2020-04-01 13 9.00 1000 2020-05-01 14 9.00 1000 2020-06-01 15 9.00 1000 2020-07-01 16 9.00 1000 2020-08-01 17 9.00 1000 2020-09-01 18 9.00 1000 2020-10-01 19 9.00 1000 2020-11-01 20 9.00 1000 2020-12-01 21 9.00 1000 2021-01-01 22 9.00 1000 2021-02-01 23 9.00 1000 2021-03-01 24 9.00 1000 2021-04-01 25 9.00 1000 2021-05-01 26 9.00 1000 2021-06-01 27 9.00 1000 2021-07-01 28 9.00 1000 2021-08-01 29 9.00 1000 2021-09-01 30 9.00 1000 2021-10-01 31 9.00 1000 2021-11-01 32 9.00 1000 2021-12-01 33 9.00 1000 2022-01-01 34 9.00 1000 2022-02-01 35 9.00 1001 2019-12-01 36 9.00 1001 2020-01-01 37 9.00 1001 2020-02-01 38 9.00 1001 2020-03-01 39 9.00 1001 2020-04-01 40 9.00 1001 2020-05-01 41 9.00 1001 2020-06-01 42 9.00 1001 2020-07-01 43 9.00 1001 2020-08-01 44 9.00 1001 2020-09-01 45 11.82 1003 2019-09-01 46 24.00 1003 2019-10-01 47 20.37 1003 2019-11-01 48 4.36 1003 2019-12-01 49 18.02 1003 2020-01-01 50 6.57 1003 2020-02-01 51 22.54 1003 2020-03-01 52 17.08 1003 2020-04-01 53 23.10 1003 2020-05-01 54 21.32 1003 2020-06-01 55 3.59 1003 2020-07-01 56 11.49 1003 2020-08-01 57 6.92 1003 2020-09-01 58 18.78 1003 2020-10-01 59 3.92 1003 2020-11-01 60 6.47 1003 2020-12-01 61 16.48 1003 2021-01-01 62 6.56 1003 2021-02-01 63 7.40 1003 2021-03-01 64 18.31 1003 2021-04-01 65 14.48 1003 2021-05-01 66 6.50 1003 2021-06-01 67 12.35 1003 2021-07-01 68 22.84 1003 2021-08-01 69 20.45 1003 2021-09-01 70 5.24 1003 2021-10-01 71 14.16 1003 2021-11-01 72 13.06 1003 2021-12-01 73 14.28 1003 2022-01-01 74 18.61 1003 2022-02-01 75 9.00 1004 2019-10-01 76 9.00 1004 2019-11-01 77 9.00 1004 2019-12-01 78 9.00 1004 2020-01-01 79 9.00 1004 2020-02-01 80 9.00 1004 2020-03-01 81 9.00 1004 2020-04-01 82 9.00 1004 2020-05-01 83 9.00 1004 2020-06-01 84 9.00 1004 2020-07-01 85 9.00 1004 2020-08-01 86 9.00 1004 2020-09-01 87 9.00 1004 2020-10-01 88 9.00 1004 2020-11-01 89 9.00 1004 2020-12-01 90 9.00 1004 2021-01-01 91 9.00 1004 2021-02-01 92 9.00 1004 2021-03-01 93 9.00 1004 2021-04-01 94 9.00 1004 2021-05-01 95 9.00 1004 2021-06-01 96 9.00 1004 2021-07-01 97 9.00 1004 2021-08-01 98 9.00 1004 2021-09-01 99 9.00 1004 2021-10-01 100 9.00 1004 2021-11-01 101 9.00 1004 2021-12-01 102 9.00 1004 2022-01-01 103 9.00 1004 2022-02-01 104 13.74 1005 2020-04-01 105 8.29 1005 2020-05-01 106 15.35 1005 2020-06-01 107 23.16 1005 2020-07-01 108 13.81 1005 2020-08-01 109 14.76 1005 2020-09-01 110 19.64 1005 2020-10-01 111 21.37 1005 2020-11-01 112 7.28 1005 2020-12-01 113 22.60 1005 2021-01-01 114 3.62 1005 2021-02-01 115 9.46 1005 2021-03-01 116 11.44 1005 2021-04-01 117 6.73 1005 2021-05-01 118 24.28 1005 2021-06-01 119 19.36 1005 2021-07-01 120 20.49 1005 2021-08-01 121 18.24 1005 2021-09-01 122 3.27 1005 2021-10-01 123 18.39 1005 2021-11-01 124 11.24 1005 2021-12-01 125 3.90 1005 2022-01-01 126 22.17 1005 2022-02-01 127 9.00 1006 2020-12-01 128 9.00 1006 2021-01-01 129 9.00 1006 2021-02-01 130 9.00 1006 2021-03-01 131 9.00 1006 2021-04-01 132 9.00 1006 2021-05-01 133 9.00 1006 2021-06-01 134 9.00 1006 2021-07-01 135 9.00 1006 2021-08-01 136 9.00 1006 2021-09-01 137 9.00 1006 2021-10-01 138 9.00 1006 2021-11-01 139 9.00 1006 2021-12-01 140 18.28 1007 2017-01-01 141 14.47 1007 2017-02-01 142 20.51 1007 2017-03-01 143 15.53 1007 2017-04-01 144 3.15 1007 2017-05-01 145 24.63 1007 2017-06-01 146 21.50 1007 2017-07-01 147 4.77 1007 2017-08-01 148 6.86 1007 2017-09-01 149 13.42 1007 2017-10-01 150 7.62 1007 2017-11-01 151 20.06 1007 2017-12-01 152 3.66 1007 2018-01-01 153 14.77 1007 2018-02-01 154 8.63 1007 2018-03-01 155 12.20 1007 2018-04-01 156 18.91 1007 2018-05-01 157 16.38 1007 2018-06-01 158 17.53 1007 2018-07-01 159 13.58 1007 2018-08-01 160 12.97 1007 2018-09-01 161 4.69 1007 